# rf504_simwstool
Organisation and simultaneous fits: using RooSimWSTool to construct a simultaneous pdf
that is built of variations of an input pdf




**Author:** Wouter Verkerke  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, May 15, 2024 at 09:51 AM.</small></i>

In [1]:
%%cpp -d
#include "RooRealVar.h"
#include "RooCategory.h"
#include "RooDataSet.h"
#include "RooGaussian.h"
#include "RooPolynomial.h"
#include "RooSimultaneous.h"
#include "RooAddPdf.h"
#include "RooWorkspace.h"
#include "RooSimWSTool.h"
#include "RooPlot.h"
#include "TCanvas.h"
#include "TAxis.h"
#include "TFile.h"
#include "TH1.h"
using namespace RooFit;

Create master pdf
---------------------------------

Construct gauss(x,m,s)

In [2]:
RooRealVar x("x", "x", -10, 10);
RooRealVar m("m", "m", 0, -10, 10);
RooRealVar s("s", "s", 1, -10, 10);
RooGaussian gauss("g", "g", x, m, s);

[#0] WARNING:InputArguments -- The parameter 's' with range [-10, 10] of the RooGaussian 'g' exceeds the safe range of (0, inf). Advise to limit its range.


Construct poly(x,p0)

In [3]:
RooRealVar p0("p0", "p0", 0.01, 0., 1.);
RooPolynomial poly("p", "p", x, p0);

Construct model = f*gauss(x) + (1-f)*poly(x)

In [4]:
RooRealVar f("f", "f", 0.5, 0., 1.);
RooAddPdf model("model", "model", RooArgSet(gauss, poly), f);

Create category observables for splitting
----------------------------------------------------------------------------------

Define two categories that can be used for splitting

In [5]:
RooCategory c("c", "c");
c.defineType("run1");
c.defineType("run2");

RooCategory d("d", "d");
d.defineType("foo");
d.defineType("bar");

Setup SimWSTool
-----------------------------

Import ingredients in a workspace

In [6]:
RooWorkspace w("w", "w");
w.import(RooArgSet(model, c, d));

[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooAddPdf::model
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooGaussian::g
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::x
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::m
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::s
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::f
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooPolynomial::p
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::p0
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooCategory::c
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooCategory::d


Make Sim builder tool

In [7]:
RooSimWSTool sct(w);

Build a simultaneous model with one split
---------------------------------------------------------------------------------

Construct a simultaneous pdf with the following form

model_run1(x) = f*gauss_run1(x,m_run1,s) + (1-f)*poly
model_run2(x) = f*gauss_run2(x,m_run2,s) + (1-f)*poly
simpdf(x,c) = model_run1(x) if c=="run1"
= model_run2(x) if c=="run2"

Returned pdf is owned by the workspace

In [8]:
RooSimultaneous *model_sim = sct.build("model_sim", "model", SplitParam("m", "c"));

Splitrule for p.d.f model with state list 
 parameter m is split with constraint in categories (c)
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: list of prototype pdfs (model)
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: list of splitting categories (c)
[#1] INFO:ObjectHandling -- RooSimPdfBuilder::executeBuild: processing prototype pdf model
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: configured customizers for all prototype pdfs
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: Customizing prototype pdf model for mode run1
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: Customizing prototype pdf model for mode run2
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooSimultaneous::model_sim
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooAddPdf::model_run1
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooGaussian::g_run1
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar:

Print tree structure of model

In [9]:
model_sim->Print("t");

0x7f4d7c139a60 RooSimultaneous::model_sim = 1 [Auto,Dirty] 
  0x7f4d7d7746c0/V- RooCategory::c = run2(idx = 1)

  0x7f4d7d8c83f0/V- RooAddPdf::model_run1 = 1/1 [Auto,Clean] 
    0x7f4d7d98da30/V- RooGaussian::g_run1 = 1 [Auto,Dirty] 
      0x7f4d7d7f8fa0/V- RooRealVar::x = 0
      0x7f4d7d9906f0/V- RooRealVar::m_run1 = 0
      0x7f4d7d8bed10/V- RooRealVar::s = 1
    0x7f4d7d868ad0/V- RooRealVar::f = 0.5
    0x7f4d7d8db840/V- RooPolynomial::p = 1 [Auto,Dirty] 
      0x7f4d7d7f8fa0/V- RooRealVar::x = 0
      0x7f4d7d7dccf0/V- RooRealVar::p0 = 0.01
  0x7f4d7d97e220/V- RooAddPdf::model_run2 = 1/1 [Auto,Clean] 
    0x7f4d7d982cf0/V- RooGaussian::g_run2 = 1 [Auto,Dirty] 
      0x7f4d7d7f8fa0/V- RooRealVar::x = 0
      0x7f4d7d985450/V- RooRealVar::m_run2 = 0
      0x7f4d7d8bed10/V- RooRealVar::s = 1
    0x7f4d7d868ad0/V- RooRealVar::f = 0.5
    0x7f4d7d8db840/V- RooPolynomial::p = 1 [Auto,Dirty] 
      0x7f4d7d7f8fa0/V- RooRealVar::x = 0
      0x7f4d7d7dccf0/V- RooRealVar::p0 = 0.01


Adjust model_sim parameters in workspace

In [10]:
w.var("m_run1")->setVal(-3);
w.var("m_run2")->setVal(+3);

Print contents of workspace

In [11]:
w.Print("v");


RooWorkspace(w) w contents

variables
---------
(c,d,f,m,m_run1,m_run2,p0,s,x)

p.d.f.s
-------
RooGaussian::g[ x=x mean=m sigma=s ] = 1
RooGaussian::g_run1[ x=x mean=m_run1 sigma=s ] = 0.011109
RooGaussian::g_run2[ x=x mean=m_run2 sigma=s ] = 0.011109
RooAddPdf::model[ f * g + [%] * p ] = 1/1
RooAddPdf::model_run1[ f * g_run1 + [%] * p ] = 0.505554/1
RooAddPdf::model_run2[ f * g_run2 + [%] * p ] = 0.505554/1
RooSimultaneous::model_sim[ indexCat=c run1=model_run1 run2=model_run2 ] = 0.505554
RooPolynomial::p[ x=x coefList=(p0) ] = 1



Build a simultaneous model with product split
-----------------------------------------------------------------------------------------

Build another simultaneous pdf using a composite split in states c X d

In [12]:
RooSimultaneous *model_sim2 = sct.build("model_sim2", "model", SplitParam("p0", "c,d"));

Splitrule for p.d.f model with state list 
 parameter p0 is split with constraint in categories (c,d)
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: list of prototype pdfs (model)
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: list of splitting categories (c,d)
[#1] INFO:ObjectHandling -- RooSimPdfBuilder::executeBuild: processing prototype pdf model
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooMultiCategory::c,d
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: configured customizers for all prototype pdfs
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: Customizing prototype pdf model for mode {run1;bar}
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: Customizing prototype pdf model for mode {run1;foo}
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: Customizing prototype pdf model for mode {run2;bar}
[#1] INFO:ObjectHandling -- RooSimWSTool::executeBuild: Customizing prototype pdf model for mode {run2;foo}
[#1] INFO:O

Print tree structure of this model

In [13]:
model_sim2->Print("t");

0x7f4d7db00cd0 RooSimultaneous::model_sim2 = 1 [Auto,Dirty] 
  0x7f4d7db1deb0/V- RooSuperCategory::model_sim2_index = {run2;foo}(idx = 1)
 [Auto,Clean] 
    0x7f4d7db1e2b0/VS RooMultiCategory::model_sim2_index_internalMultiCat = {run2;foo}(idx = 1)
 [Auto,Clean] 
      0x7f4d7d7746c0/VS RooCategory::c = run2(idx = 1)

      0x7f4d7d4d0500/VS RooCategory::d = foo(idx = 0)

  0x7f4d7db1e6e0/V- RooAddPdf::model_{run1;bar} = 1/1 [Auto,Clean] 
    0x7f4d7d91b060/V- RooGaussian::g = 1 [Auto,Dirty] 
      0x7f4d7d7f8fa0/V- RooRealVar::x = 0
      0x7f4d7d8c12e0/V- RooRealVar::m = 0
      0x7f4d7d8bed10/V- RooRealVar::s = 1
    0x7f4d7d868ad0/V- RooRealVar::f = 0.5
    0x7f4d7db11410/V- RooPolynomial::p_{run1;bar} = 1 [Auto,Dirty] 
      0x7f4d7d7f8fa0/V- RooRealVar::x = 0
      0x7f4d7db139a0/V- RooRealVar::p0_{run1;bar} = 0.01
  0x7f4d7db13f90/V- RooAddPdf::model_{run1;foo} = 1/1 [Auto,Clean] 
    0x7f4d7d91b060/V- RooGaussian::g = 1 [Auto,Dirty] 
      0x7f4d7d7f8fa0/V- RooRealVar::x = 0
  